<a href="https://colab.research.google.com/github/sclaudiobr/covid2019/blob/master/COVID19_Heatmap.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
!pip install --upgrade folium
!pip install geobr

In [2]:
import pandas as pd
import numpy as np
import folium
from folium import plugins
import json
import geobr as br
print("Nova versão do Folium: ", folium.__version__)

Nova versão do Folium:  0.11.0


In [94]:
import requests
r =requests.get('https://data.brasil.io/dataset/covid19/caso.csv.gz', allow_redirects=True)
open('caso.csv.gz', 'wb').write(r.content)
df = pd.read_csv("caso.csv.gz", compression='gzip')
cidades = br.read_municipal_seat(year=2010)

In [19]:
# Aqui fazemos a troca de índice de cidades pelo códifo do IBGE
cidades = cidades.set_index('code_muni')

In [96]:
cidades.head()

name_muni code_state  ...  year                     geometry
code_muni                                    ...                                   
1100015.0  Alta Floresta D'oeste         11  ...  2010  POINT (-61.99982 -11.93554)
1100023.0              Ariquemes         11  ...  2010   POINT (-63.03327 -9.90846)
1100031.0                 Cabixi         11  ...  2010  POINT (-60.54431 -13.49976)
1100049.0                 Cacoal         11  ...  2010  POINT (-61.44294 -11.43387)
1100056.0             Cerejeiras         11  ...  2010  POINT (-60.81843 -13.19503)

[5 rows x 7 columns]

In [24]:
cities = df.loc[df.place_type == 'city',:]

cities.place_type.unique()

array(['city'], dtype=object)

In [25]:
# juntar as duas bases de dados (IBGE cidades) come guardar na variável cities
cities = cities.join(cidades, on='city_ibge_code')

date state  ...  year                     geometry
291      2020-12-31    AC  ...  2010  POINT (-67.05232 -10.07379)
292      2020-12-30    AC  ...  2010  POINT (-67.05232 -10.07379)
293      2020-12-29    AC  ...  2010  POINT (-67.05232 -10.07379)
294      2020-12-28    AC  ...  2010  POINT (-67.05232 -10.07379)
295      2020-12-27    AC  ...  2010  POINT (-67.05232 -10.07379)
...             ...   ...  ...   ...                          ...
1233415  2020-06-23    SP  ...  2010  POINT (-49.34095 -22.94458)
1233416  2020-06-22    SP  ...  2010  POINT (-49.34095 -22.94458)
1233417  2020-06-21    SP  ...  2010  POINT (-49.34095 -22.94458)
1233418  2020-06-20    SP  ...  2010  POINT (-49.34095 -22.94458)
1233419  2020-06-19    SP  ...  2010  POINT (-49.34095 -22.94458)

[1225554 rows x 20 columns]

In [30]:
cities.geometry

291        POINT (-67.05232 -10.07379)
292        POINT (-67.05232 -10.07379)
293        POINT (-67.05232 -10.07379)
294        POINT (-67.05232 -10.07379)
295        POINT (-67.05232 -10.07379)
                      ...             
1233415    POINT (-49.34095 -22.94458)
1233416    POINT (-49.34095 -22.94458)
1233417    POINT (-49.34095 -22.94458)
1233418    POINT (-49.34095 -22.94458)
1233419    POINT (-49.34095 -22.94458)
Name: geometry, Length: 1225554, dtype: geometry

In [37]:
type(cities)

pandas.core.frame.DataFrame

In [61]:
import geopandas as gpd
gdf = gpd.GeoDataFrame(cities, crs="EPSG:4326")
gdf['latitude'] = gdf.geometry.y
gdf['longitude'] = gdf.geometry.x
cities = gdf

/usr/local/lib/python3.6/dist-packages/ipykernel_launcher.py:2: FutureWarning: CRS mismatch between CRS of the passed geometries and 'crs'. Use 'GeoDataFrame.set_crs(crs, allow_override=True)' to overwrite CRS or 'GeoDataFrame.to_crs(crs)' to reproject geometries. CRS mismatch will raise an error in the future versions of GeoPandas.
  


In [62]:
# selecionar as colunas de interesse da tabela "cities", 
# geo_last são os ultimos registros da tabela para cada cidade
geo_last = cities.loc[cities.is_last==True,['city','latitude', 'longitude','state','confirmed','deaths']]
geo_last.head()

city   latitude  longitude state  confirmed  deaths
291     Acrelândia -10.073794 -67.052317    AC        563      12
564   Assis Brasil -10.942866 -69.563459    AC        762       9
804      Brasiléia -11.016411 -68.747943    AC       1298      22
1036        Bujari  -9.820020 -67.951859    AC        491       8
1299      Capixaba -10.569768 -67.673508    AC        305       8

In [63]:
#Quantidade de cidades com casos de covid-19
len(geo_last)

5589

In [64]:
#Quantidade de casos confirmados 
geo_last.confirmed.sum()

7534823

In [53]:
#Quantidade de mortes por covid-19
geo_last.deaths.sum()

192263

In [65]:
#Porcentagem de mortos sobre os casos confirmados
geo_last.deaths.sum()/geo_last.confirmed.sum()*100

2.5516591431543914

In [66]:
# verificar se todos os estados estão inseridos
len(geo_last.state.unique())

27

In [67]:
# Separando o conjunto de dados da interpolação
coordenadas = geo_last[['latitude','longitude','confirmed']]
#retirar as linhas que tiver dados faltando
coordenadas = coordenadas.dropna()
coordenadas.head()

latitude  longitude  confirmed
291  -10.073794 -67.052317        563
564  -10.942866 -69.563459        762
804  -11.016411 -68.747943       1298
1036  -9.820020 -67.951859        491
1299 -10.569768 -67.673508        305

In [68]:
baseMap = folium.Map(
    width = '100%',   height = '100%',
    location = [-15.77972, -47.92972], # <- Brasil
    zoom_start = 4
)

In [ ]:
baseMap

In [69]:
baseMap = baseMap.add_child(plugins.HeatMap(coordenadas))

In [70]:
baseMap

In [71]:
# retirar dados faltantes
geo_last = geo_last.dropna()
geo_last.head(5)

city   latitude  longitude state  confirmed  deaths
291     Acrelândia -10.073794 -67.052317    AC        563      12
564   Assis Brasil -10.942866 -69.563459    AC        762       9
804      Brasiléia -11.016411 -68.747943    AC       1298      22
1036        Bujari  -9.820020 -67.951859    AC        491       8
1299      Capixaba -10.569768 -67.673508    AC        305       8

In [72]:
for i in range(0,len(geo_last)):
    folium.Circle(
        location = [geo_last.iloc[i]['latitude'], geo_last.iloc[i]['longitude']],
        color = '#00FF69',
        fill = '#00A1B3',
        tooltip = '<li><bold> CIDADE: '+ str(geo_last.iloc[i]['city']) + "</li></bold>" +
                 '<li><bold> ESTADO: '+ str(geo_last.iloc[i]['state']) +"</li></bold>" +
                 '<li><bold> CONFIRMADOS: '+ str(geo_last.iloc[i]['confirmed'])+"</li></bold>" +
                 '<li><bold> MORTES: '+ str(geo_last.iloc[i]['deaths']) + "</li></bold>" ,
        radius = (geo_last.iloc[i]['confirmed']**0.78)
                                            
    ).add_to(baseMap)
#baseMap

In [73]:
# importando logomarca e colocando no mapa
from folium.plugins import FloatImage
url = 'https://raw.githubusercontent.com/sclaudiobr/algoritmos-py/master/text43.png'
FloatImage(url,bottom=10,left=55).add_to(baseMap)
baseMap

In [74]:
baseMap.save('heatmap-cidade.html')